# Identitas Mahasiswa
### Applied Data Science for Business

| <span style="color:blue"> Nama Lengkap </span> | <span style="color:blue"> Nama Panggilan </span> | <span style="color:blue"> NIM </span> |
| :--- | :---: | :---: |
| Ariq Irfansyah Pratama | Ariq | 23101910032 |
| David Hansel Gunawan | David | 23101910071
| Jonathan Christopher| Jonathan | 23101910043 
| Kayleen Mirabel | Kayleen | 23101910044|
| Richelle Antares | Richelle| 23101910011|

# Preparation

In [1]:
#! pip install statsmodels

## Importing Packages

Pertama-tama, kami mengimport package-package yang dibutuhkan terlebih dahulu.

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.model_selection import train_test_split
import h2o
from pandas_profiling import ProfileReport
import statsmodels.api as sm

from sklearn.metrics import classification_report,confusion_matrix
from sklearn.model_selection import cross_val_score
from sklearn.linear_model import LogisticRegression

from sklearn.ensemble import AdaBoostClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from h2o.estimators.random_forest import H2ORandomForestEstimator
from h2o.estimators.gbm import H2OGradientBoostingEstimator

## Initializing H2O

Menjalankan H2O di port 8080 dan parameter 'bind to localhost' False agar H2O tetap dapat dipakai di luar Deepnote.

In [3]:
h2o.init(port=8080, bind_to_localhost=False)

Checking whether there is an H2O instance running at http://localhost:8080 ..... not found.
Attempting to start a local H2O server...
  Java Version: java version "18.0.1.1" 2022-04-22; Java(TM) SE Runtime Environment (build 18.0.1.1+2-6); Java HotSpot(TM) 64-Bit Server VM (build 18.0.1.1+2-6, mixed mode, sharing)
  Starting server from /opt/anaconda3/lib/python3.9/site-packages/h2o/backend/bin/h2o.jar
  Ice root: /var/folders/j3/ws9ldyjs5j12kfh6b2xt4v7w0000gn/T/tmp2h6tava2
  JVM stdout: /var/folders/j3/ws9ldyjs5j12kfh6b2xt4v7w0000gn/T/tmp2h6tava2/h2o_ariqirfansyah_started_from_python.out
  JVM stderr: /var/folders/j3/ws9ldyjs5j12kfh6b2xt4v7w0000gn/T/tmp2h6tava2/h2o_ariqirfansyah_started_from_python.err
  Server is running at http://127.0.0.1:8080
Connecting to H2O server at http://127.0.0.1:8080 ... successful.


--------------------------  ------------------------------------
H2O_cluster_uptime:         03 secs
H2O_cluster_timezone:       Asia/Jakarta
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.36.1.2
H2O_cluster_version_age:    1 month and 17 days
H2O_cluster_name:           H2O_from_python_ariqirfansyah_uvqnh9
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    2 Gb
H2O_cluster_total_cores:    8
H2O_cluster_allowed_cores:  8
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://127.0.0.1:8080
H2O_connection_proxy:       {"http": null, "https": null}
H2O_internal_security:      False
Python_version:             3.9.12 final
--------------------------  ------------------------------------

## Defining Useful Functions

#### Kami juga memasukkan beberapa fungsi yang berguna dalam laporan ini.

Fungsi pertama adalah assign. Fungsi ini dapat digunakan untuk mengganti suatu nilai berdasarkan kondisi tertentu. Kondisi tersebut dapat ditetapkan sendiri atau dengan menentukan rentang jumlah. Jika nilai tertentu dalam suatu kolom memiliki jumlah di antara nilai yang ditentukan. Misalnya, huruf a hanya ada satu, sedangkan jumlah yang diinginkan adalah minimal 5. Maka dengan menggunakan fungsi ini, a dapat diganti dengan nilai yang diinginkan. Fungsi ini berguna untuk melakukan binning terhadap nilai atau kategori yang jumlahnya hanya sedikit.

In [4]:
def assign(data, column, ran, values, show=True, con=False, cat=True, ret=True):
    if bool(con):
        conditions=con
        ran=False
    else:
        conditions = []
        ran = list(set(ran))
        ran.sort(reverse=True)
        for i in range(len(ran) - 1):
            conditions.append(np.where(np.logical_and(data[column].value_counts() <= ran[i],
                                                      data[column].value_counts() > ran[i+1]),
                                       data[column].value_counts().index,
                                       np.nan))
    if show:
        print(f'Column: {column}')
    for i, j, k in zip(conditions, values, range(len(conditions))):
        index = data[data[column].isin(i)].index
        data.loc[index, column] = j
        if show and bool(ran):
            print(f'{len(index)}\treplaced by {j}\twith condition {ran[k+1]}{" "*(5-len(str(ran[k+1])))}< value_counts <= {ran[k]}')
    if show:
        print(data[column].value_counts())
    if cat:
        data[column] = data[column].astype('category')
    if ret:
        return conditions

Fungsi kedua adalah timer. Fungsi ini berguna untuk menghitung lama suatu kode dijalankan.

In [6]:
def timer(start_time, header='\nProgram Schedule'):
    end_time = pd.to_datetime('now') + pd.Timedelta('07:00:00')
    print(header)
    print(start_time.strftime('Start   : %Y-%m-%d %I:%M:%S %p'))
    print(end_time.strftime('Finish  : %Y-%m-%d %I:%M:%S %p'))
    run_time = str(end_time - start_time)
    idx1 = run_time.find(' ', 3) + 1
    idx2 = run_time.find('.')
    print('Runtime :', run_time[idx1 : idx2], '\n')

## Importing Data Training and Dropping Useless Columns

Selanjutnya, kami mengimport data yang akan digunakan. Kami langsung menghilangkan nan pada data ini karena proporsi nan di data ini sangat kecil dibandingkan dengan keseluruhan datanya. Selain itu, kolom Transaction_ID di-drop karena setiap row unik serta Transaction_Flag dan Bank_ID juga di-drop karena semuanya juga sama. Dropna dan drop kolom menggunakan True pada parameter inplace agar modifikasi tersebut langsung dilakukan pada dataframe tersebut tanpa membuat dataframe baru.

In [7]:
df = pd.read_excel('cctx_train.xlsx')
df.dropna(inplace=True)
df.drop(['Transaction_ID', 'Transaction_Flag', 'Bank_ID'], axis=1, inplace=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10484 entries, 0 to 10499
Data columns (total 18 columns):
 #   Column                         Non-Null Count  Dtype         
---  ------                         --------------  -----         
 0   Transaction_Date               10484 non-null  datetime64[ns]
 1   Transaction_Type               10484 non-null  object        
 2   Transaction_Amount             10484 non-null  float64       
 3   CC_ID                          10484 non-null  object        
 4   Card_Type                      10484 non-null  object        
 5   Card_Holder                    10484 non-null  int64         
 6   Channel_ID                     10484 non-null  int64         
 7   Merchant_ID                    10484 non-null  object        
 8   Country_ID                     10484 non-null  object        
 9   City_ID                        10484 non-null  object        
 10  EDC_Type                       10484 non-null  object        
 11  EDC_Location   

Menampilkan 5 baris teratas pada dataframe.

In [8]:
df.head()

Transaction_Date Transaction_Type  Transaction_Amount     CC_ID  \
0 2018-01-01 01:48:50.951              T08             50000.0  CCID5563   
1 2018-01-01 09:08:52.666              T01           1000000.0  CCID4598   
2 2018-01-01 09:08:52.666              T15           1000000.0  CCID2839   
3 2018-01-01 09:45:55.969              T15           1000000.0  CCID2968   
4 2018-01-01 23:41:59.228              T10           2500000.0  CCID0176   

  Card_Type  Card_Holder  Channel_ID Merchant_ID Country_ID    City_ID  \
0      CC11            2           1       M0001      CTY06  CTY06-133   
1      CC08            2           1       M0001      CTY06  CTY06-129   
2      CC08            2           1       M0001      CTY06  CTY06-073   
3      CC08            2           1       M0001      CTY06  CTY06-129   
4      CC12            2           1       M0001      CTY06  CTY06-133   

  EDC_Type EDC_Location EDC_Owner  Average_Transaction_Amount  \
0  EDC0885     LEDC3703  OEDC0377                   661855.03   
1  EDC0565     LEDC3205  OEDC0377                  2171907.10   
2  EDC4639     LEDC3081  OEDC0377                  1714437.98   
3  EDC3918     LEDC1993  OEDC0377                 10163708.23   
4  EDC2863     LEDC2062  OEDC0377                   690066.65   

   Maximum_Transaction_Amount  Minimum_Transaction_Amount  \
0                  11000000.0                     24212.0   
1                  28555000.0                    100000.0   
2                   8500000.0                        50.0   
3                 100000000.0                     63000.0   
4                   3523000.0                     26500.0   

   Average_Transaction_Frequency  Fraud_Status  
0                           2.91             0  
1                           3.12             1  
2                           3.58             0  
3                           2.57             0  
4                           4.23             0

# Binning Train Data

### City ID

Menampilkan value counts dari kolom City_ID untuk melihat jumlah dari tiap kategori pada kolom tersebut.

In [9]:
df['City_ID'].value_counts()

CTY06-023    4247
CTY06-133    1276
CTY06-181     800
CTY06-171     440
CTY06-186     337
             ... 
CTY06-106       1
CTY09-002       1
CTY06-161       1
CTY06-078       1
CTY06-019       1
Name: City_ID, Length: 227, dtype: int64

Menampilkan semua kategori (unik) dari kolom City_ID.

In [10]:
df['City_ID'].unique()

array(['CTY06-133', 'CTY06-129', 'CTY06-073', 'CTY06-023', 'CTY06-181',
       'CTY06-083', 'CTY06-173', 'CTY06-149', 'CTY06-004', 'CTY06-194',
       'CTY06-171', 'CTY06-096', 'CTY06-035', 'CTY06-186', 'CTY06-174',
       'CTY06-092', 'CTY06-029', 'CTY06-128', 'CTY06-101', 'CTY06-087',
       'CTY06-046', 'CTY06-197', 'CTY06-125', 'CTY06-056', 'CTY06-089',
       'CTY06-058', 'CTY06-099', 'CTY06-005', 'CTY06-180', 'CTY06-112',
       'CTY06-151', 'CTY06-176', 'CTY13-003', 'CTY06-049', 'CTY06-175',
       'CTY06-071', 'CTY06-140', 'CTY06-121', 'CTY06-090', 'CTY06-115',
       'CTY06-110', 'CTY06-195', 'CTY06-120', 'CTY06-164', 'CTY06-205',
       'CTY06-179', 'CTY06-126', 'CTY06-152', 'CTY06-039', 'CTY06-075',
       'CTY06-077', 'CTY06-166', 'CTY06-113', 'CTY06-148', 'CTY06-190',
       'CTY06-082', 'CTY06-067', 'CTY06-137', 'CTY06-147', 'CTY06-167',
       'CTY06-001', 'CTY06-097', 'CTY06-072', 'CTY06-086', 'CTY06-191',
       'CTY06-124', 'CTY06-189', 'CTY06-013', 'CTY06-185', 'CTY0

Menampilkan jumlah baris pada kolom City_ID yang memuat CTY06.

In [11]:
df['City_ID'].str.contains(pat='CTY06').value_counts()

True     10448
False       36
Name: City_ID, dtype: int64

Menampilkan jumlah baris pada kolom Country_ID yang memuat CTY06. Hasilnya sudah pasti sama dengan kode di atas karena setiap baris dari kolom City_ID juga berisi nilai dari kolom Country ID masing-masing. Misal CTY06-104 pada City_ID memiliki CTY06 dari kolom Country_ID. Dari sini terlihat bahwa hanya ada 36 baris yang merupakan kota dari negara selain CTY06.

In [12]:
df['Country_ID'].str.contains(pat='CTY06').value_counts()

True     10448
False       36
Name: Country_ID, dtype: int64

Membandingkan jumlah baris pada kolom City_ID yang memiliki CTY06 dengan jumlah baris pada kolom Country_ID  yang memiliki CTY06. Di sini terlihat bahwa jumlah nilainya seharusnya sama dengan jumlah True pada kolom di atas.

In [13]:
(df['City_ID'].str.contains(pat='CTY06') == 
 df['Country_ID'].str.contains(pat='CTY06')).value_counts()

True    10484
dtype: int64

Menggunakan fungsi assign untuk mengganti kategori Country_ID yang berjumlah di antara 0 dan 100 menjadi asing, serta di antara 100 dan 20000 menjadi Indonesia.

In [14]:
col = 'Country_ID'
ran = [0, 100, 20_000]
val = ['Indonesia', 'Asing']
con_Country_ID = assign(df, col, ran, val)

Column: Country_ID
10448	replaced by Indonesia	with condition 100  < value_counts <= 20000
36	replaced by Asing	with condition 0    < value_counts <= 100
Indonesia    10448
Asing           36
Name: Country_ID, dtype: int64


Country selain CTY06 dianggap sebagai negara lain.

### EDC Type

Melihat jumlah dari tiap kategori pada kolom EDC_Type.

In [15]:
df['EDC_Type'].value_counts()

EDC0002    705
EDC1846     25
EDC0729     17
EDC1155     17
EDC0798     16
          ... 
EDC2558      1
EDC4631      1
EDC4342      1
EDC4846      1
EDC4477      1
Name: EDC_Type, Length: 4787, dtype: int64

Kategori dengan jumlah di antara 0 dan 10 akan diganti menjadi GPRS, kategori dengan jumlah di antara 10 dan 100 akan diganti menjadi Mobile, serta kategori dengan jumlah di antara 100 dan 1000 akan diganti menjadi kategori Bank.

In [16]:
col = 'EDC_Type'
ran = [0, 10, 100, 1_000]
val = ['Bank', 'Mobile', 'GPRS']
con_EDC_Type = assign(df, col, ran, val)

Column: EDC_Type
705	replaced by Bank	with condition 100  < value_counts <= 1000
365	replaced by Mobile	with condition 10   < value_counts <= 100
9414	replaced by GPRS	with condition 0    < value_counts <= 10
GPRS      9414
Bank       705
Mobile     365
Name: EDC_Type, dtype: int64


Pemilihan range hanya berdasarkan pemikiran kelompok. Karena yang terbanyak hanya 705, maka kelompok memutuskan menjadikan EDC_Type tersebut bekerja sama dengan pihak bank, karena data ini berasal hanya dari satu bank saja. Selanjutnya, untuk EDC GPRS berjumlah banyak dan dijadikan satu karena biasa EDC GPRS sering dijumpai di gerai-gerai kecil. Sementara, untuk EDC Mobile merupakan EDC GPRS yang menggunakan baterai (tidak menggunakan kabel) yang masih kelompok kira jarang ditemui sehingga dikelompokkan menjadi satu.

### EDC Owner

Melihat jumlah dari tiap kategori pada kolom EDC_Owner.

In [17]:
df['EDC_Owner'].value_counts()

OEDC0377    8312
OEDC0378      15
OEDC0212       6
OEDC1363       6
OEDC0886       6
            ... 
OEDC0530       1
OEDC0721       1
OEDC1412       1
OEDC1497       1
OEDC1557       1
Name: EDC_Owner, Length: 1460, dtype: int64

Kategori dengan jumlah di antara 0 dan 100 akan diganti menjadi sewa dan kategori dengan jumlah di antara 100 dan 10000 akan diganti menjadi pemilik

In [18]:
col = 'EDC_Owner'
ran = [0, 100, 10_000]
val = ['Pemilik', 'Sewa']
con_EDC_Owner = assign(df, col, ran, val)

Column: EDC_Owner
8312	replaced by Pemilik	with condition 100  < value_counts <= 10000
2172	replaced by Sewa	with condition 0    < value_counts <= 100
Pemilik    8312
Sewa       2172
Name: EDC_Owner, dtype: int64


Kelompok mengelompokkan EDC Owner menjadi pemilik dan penyewa karena beranggapan bahwa yang berjumlah 8000 merupakan pemilik.

### Transaction Type

Melihat jumlah dari tiap kategori pada kolom Transaction_Type.

In [19]:
df['Transaction_Type'].value_counts()

T01    2866
T15    2447
T02    1323
T08    1072
T13     768
T06     675
T14     509
T04     263
T03     206
T10     112
T12      77
T11      50
T20      29
T17      27
T05      22
T16      12
T09       8
T19       7
T07       7
T18       4
Name: Transaction_Type, dtype: int64

Kategori dengan jumlah di antara 0 hingga 100 akan diganti menjadi Jarang, kategori dengan jumlah di antara 100 hingga 1000 dijadikan Umum, serta kategori dengan jumlah di antara 1000 hingga 10000 akan dijadikan kategori Sering.

In [20]:
col = 'Transaction_Type'
ran = [0, 100, 1_000, 10_000]
val = ['Sering', 'Umum', 'Jarang']
con_Transaction_Type = assign(df, col, ran, val)

Column: Transaction_Type
7708	replaced by Sering	with condition 1000 < value_counts <= 10000
2533	replaced by Umum	with condition 100  < value_counts <= 1000
243	replaced by Jarang	with condition 0    < value_counts <= 100
Sering    7708
Umum      2533
Jarang     243
Name: Transaction_Type, dtype: int64


Transaksi dikelompokkan berdasarkan frekuensinya.

### Card Type

Melihat jumlah dari tiap kategori pada kolom Card_Type.

In [21]:
df['Card_Type'].value_counts()

CC11    3835
CC08    2106
CC09    1379
CC00    1260
CC10    1092
CC04     237
CC02     157
CC01     155
CC05     145
CC12      54
CC13      36
CC03      20
CC06       7
CC07       1
Name: Card_Type, dtype: int64

Melakukan groupby terhadap kolom Card Type dengan melihat agregat jumlah baris, standard deviasi, nilai minimum, dan nilai maksimum dari tiap kategori Card_Type. Kemudian, hasil tersebut di-sort berdasarkan nilai Maximum Transaction Amount dari yang terbesar ke terkecil.

In [22]:
cc = df.groupby(['Card_Type']).agg({'Maximum_Transaction_Amount': ['count', 'std', 'min', 'max']}).sort_values(('Maximum_Transaction_Amount', 'max'), ascending=False)
cc

Maximum_Transaction_Amount                                       
                               count           std         min          max
Card_Type                                                                  
CC02                             157  2.455402e+07   1000000.0  100000000.0
CC05                             145  1.118061e+07    500000.0  100000000.0
CC08                            2106  2.571725e+07    700000.0  100000000.0
CC04                             237  1.302443e+07    500000.0   75000000.0
CC10                            1092  6.384819e+06    100000.0   69750000.0
CC11                            3835  9.627690e+06    243000.0   69750000.0
CC00                            1260  9.274332e+06    300000.0   58090000.0
CC09                            1379  5.554187e+06     38000.0   56161050.0
CC01                             155  8.910502e+06    500000.0   50000000.0
CC03                              20  1.601625e+07    500000.0   50000000.0
CC06                               7  1.881146e+07   1500000.0   50000000.0
CC13                              36  9.231345e+06    100000.0   50000000.0
CC12                              54  8.975019e+06    750000.0   46000000.0
CC07                               1           NaN  12500000.0   12500000.0

Menentukan kondisi untuk fungsi assign, dimana 3 kategori teratas dari hasil groupby di atas akan dijadikan sebagai kondisi pertama, kategori keempat sampai kedelapan akan dijadikan kondisi kedua, serta kategori kesembilan sampai yang terakhir akan dijadikan sebagai kategori ketiga. Kondisi ini dibuat berdasarkan urutan limit transaksi karena dataframe di atas sudah diurutkan berdasarkan nilai maksimal transaksi.

In [23]:
con_Card_Type = [cc[ :3].index,
                 cc[3:8].index,
                 cc[8: ].index] #val = ['Platinum', 'Gold', 'Silver']
con_Card_Type

[Index(['CC02', 'CC05', 'CC08'], dtype='object', name='Card_Type'),
 Index(['CC04', 'CC10', 'CC11', 'CC00', 'CC09'], dtype='object', name='Card_Type'),
 Index(['CC01', 'CC03', 'CC06', 'CC13', 'CC12', 'CC07'], dtype='object', name='Card_Type')]

Melakukan assign terhadap kolom Card_Type berdasarkan kondisi di atas. Kondisi pertama dikategorikan sebagai Platinum, kondisi kedua dikategorikan sebagai Gold, dan kondisi ketiga dikategorikan sebagai Silver.

In [24]:
col = 'Card_Type'
ran = False
val = ['Platinum', 'Gold', 'Silver']
assign(df, col, ran, val, con=con_Card_Type, ret=False)

Column: Card_Type
Gold        7803
Platinum    2408
Silver       273
Name: Card_Type, dtype: int64


### Channel ID

Melihat jumlah dari tiap kategori pada kolom Channel_ID.

In [25]:
df['Channel_ID'].value_counts()

1    8312
2    1462
5     680
3      25
4       5
Name: Channel_ID, dtype: int64

Kategori dengan jumlah di antara 0 hingga 8000 akan diganti menjadi Sekunder, sedangkan kategori dengan jumlah di antara 8000 hingga 10000 dijadikan Primer.

In [26]:
col = 'Channel_ID'
ran = [0, 8_000, 10_000]
val = ['Primer', 'Sekunder']
con_Channel_ID = assign(df, col, ran, val)

Column: Channel_ID
8312	replaced by Primer	with condition 8000 < value_counts <= 10000
2172	replaced by Sekunder	with condition 0    < value_counts <= 8000
Primer      8312
Sekunder    2172
Name: Channel_ID, dtype: int64


### Merchant ID

Melihat jumlah dari tiap kategori pada kolom Merchant_ID.

In [27]:
df['Merchant_ID'].value_counts()

M0001    9022
M0243       6
M0063       6
M0140       6
M0100       6
         ... 
M0873       1
M0697       1
M0848       1
M1071       1
M0597       1
Name: Merchant_ID, Length: 974, dtype: int64

Kategori dengan jumlah di antara 0 hingga 9000 akan diganti menjadi Sekunder, sedangkan kategori dengan jumlah di antara 9000 hingga 10000 dijadikan Primer.

In [28]:
col = 'Merchant_ID'
ran = [0, 9_000, 10_000]
val = ['Primer', 'Sekunder']
con_Merchant_ID = assign(df, col, ran, val)

Column: Merchant_ID
9022	replaced by Primer	with condition 9000 < value_counts <= 10000
1462	replaced by Sekunder	with condition 0    < value_counts <= 9000
Primer      9022
Sekunder    1462
Name: Merchant_ID, dtype: int64


### Card Holder

Melihat jumlah dari tiap kategori pada kolom Card_Holder.

In [29]:
df['Card_Holder'].value_counts()

2    9774
1     710
Name: Card_Holder, dtype: int64

Kategori dari kolom Card_Holder sudah terpisah dengan rapi, sehingga Card_Holder dengan nilai 2 akan dijadikan Primer, sedangkan Card_Holder dengan nilai 1 akan dijadikan Sekunder.

In [30]:
df.loc[df[df['Card_Holder'] == 2].index, 'Card_Holder'] = 'Primer'
df.loc[df[df['Card_Holder'] == 1].index, 'Card_Holder'] = 'Sekunder'
df['Card_Holder'] = df['Card_Holder'].astype('category')
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10484 entries, 0 to 10499
Data columns (total 18 columns):
 #   Column                         Non-Null Count  Dtype         
---  ------                         --------------  -----         
 0   Transaction_Date               10484 non-null  datetime64[ns]
 1   Transaction_Type               10484 non-null  category      
 2   Transaction_Amount             10484 non-null  float64       
 3   CC_ID                          10484 non-null  object        
 4   Card_Type                      10484 non-null  category      
 5   Card_Holder                    10484 non-null  category      
 6   Channel_ID                     10484 non-null  category      
 7   Merchant_ID                    10484 non-null  category      
 8   Country_ID                     10484 non-null  category      
 9   City_ID                        10484 non-null  object        
 10  EDC_Type                       10484 non-null  category      
 11  EDC_Location   

Melihat data yang sudah selesai di-binning.

In [31]:
df.head()

Transaction_Date Transaction_Type  Transaction_Amount     CC_ID  \
0 2018-01-01 01:48:50.951           Sering             50000.0  CCID5563   
1 2018-01-01 09:08:52.666           Sering           1000000.0  CCID4598   
2 2018-01-01 09:08:52.666           Sering           1000000.0  CCID2839   
3 2018-01-01 09:45:55.969           Sering           1000000.0  CCID2968   
4 2018-01-01 23:41:59.228             Umum           2500000.0  CCID0176   

  Card_Type Card_Holder Channel_ID Merchant_ID Country_ID    City_ID EDC_Type  \
0      Gold      Primer     Primer      Primer  Indonesia  CTY06-133     GPRS   
1  Platinum      Primer     Primer      Primer  Indonesia  CTY06-129     GPRS   
2  Platinum      Primer     Primer      Primer  Indonesia  CTY06-073     GPRS   
3  Platinum      Primer     Primer      Primer  Indonesia  CTY06-129     GPRS   
4    Silver      Primer     Primer      Primer  Indonesia  CTY06-133     GPRS   

  EDC_Location EDC_Owner  Average_Transaction_Amount  \
0     LEDC3703   Pemilik                   661855.03   
1     LEDC3205   Pemilik                  2171907.10   
2     LEDC3081   Pemilik                  1714437.98   
3     LEDC1993   Pemilik                 10163708.23   
4     LEDC2062   Pemilik                   690066.65   

   Maximum_Transaction_Amount  Minimum_Transaction_Amount  \
0                  11000000.0                     24212.0   
1                  28555000.0                    100000.0   
2                   8500000.0                        50.0   
3                 100000000.0                     63000.0   
4                   3523000.0                     26500.0   

   Average_Transaction_Frequency  Fraud_Status  
0                           2.91             0  
1                           3.12             1  
2                           3.58             0  
3                           2.57             0  
4                           4.23             0

Melakukan feature engineering dengan membuat kolom Range yang merupakan hasil pengurangan dari kolom Maximum Transaction Amount dengan kolom Minimum Transaction Amount.

In [32]:
df['Range'] = df['Maximum_Transaction_Amount'] - df['Minimum_Transaction_Amount']

Melihat informasi dasar dari data final.

In [33]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10484 entries, 0 to 10499
Data columns (total 19 columns):
 #   Column                         Non-Null Count  Dtype         
---  ------                         --------------  -----         
 0   Transaction_Date               10484 non-null  datetime64[ns]
 1   Transaction_Type               10484 non-null  category      
 2   Transaction_Amount             10484 non-null  float64       
 3   CC_ID                          10484 non-null  object        
 4   Card_Type                      10484 non-null  category      
 5   Card_Holder                    10484 non-null  category      
 6   Channel_ID                     10484 non-null  category      
 7   Merchant_ID                    10484 non-null  category      
 8   Country_ID                     10484 non-null  category      
 9   City_ID                        10484 non-null  object        
 10  EDC_Type                       10484 non-null  category      
 11  EDC_Location   

Memunculkan dummy variable dan melakukan drop terhadap kolom yang tidak akan digunakan. Kolom Transaction_Date akan dibuang karena tidak relevan. Kolom CC_ID dan EDC_Location dibuang karena nilai dari tiap baris terlalu unik. 

In [34]:
df2=pd.get_dummies(df.drop(['Transaction_Date', 'CC_ID', 'EDC_Location','City_ID'], axis=1))

Memunculkan dataframe yang sudah berisi dummy variable.

In [35]:
df2

Transaction_Amount  Average_Transaction_Amount  \
0                 50000.0                   661855.03   
1               1000000.0                  2171907.10   
2               1000000.0                  1714437.98   
3               1000000.0                 10163708.23   
4               2500000.0                   690066.65   
...                   ...                         ...   
10495           5000000.0                  1667486.67   
10496           4800000.0                  2530285.33   
10497           2500000.0                  1225000.00   
10498           1100000.0                   820036.79   
10499            102500.0                   571282.15   

       Maximum_Transaction_Amount  Minimum_Transaction_Amount  \
0                      11000000.0                     24212.0   
1                      28555000.0                    100000.0   
2                       8500000.0                        50.0   
3                     100000000.0                     63000.0   
4                       3523000.0                     26500.0   
...                           ...                         ...   
10495                  20000000.0                     50000.0   
10496                   5000000.0                   1000000.0   
10497                  10000000.0                    100000.0   
10498                   4000000.0                     50000.0   
10499                   5000000.0                     25000.0   

       Average_Transaction_Frequency  Fraud_Status       Range  \
0                               2.91             0  10975788.0   
1                               3.12             1  28455000.0   
2                               3.58             0   8499950.0   
3                               2.57             0  99937000.0   
4                               4.23             0   3496500.0   
...                              ...           ...         ...   
10495                           4.15             0  19950000.0   
10496                           1.64             0   4000000.0   
10497                           1.97             0   9900000.0   
10498                           3.16             0   3950000.0   
10499                           2.36             0   4975000.0   

       Transaction_Type_Jarang  Transaction_Type_Sering  \
0                            0                        1   
1                            0                        1   
2                            0                        1   
3                            0                        1   
4                            0                        0   
...                        ...                      ...   
10495                        0                        0   
10496                        0                        0   
10497                        0                        0   
10498                        0                        0   
10499                        0                        1   

       Transaction_Type_Umum  ...  Channel_ID_Sekunder  Merchant_ID_Primer  \
0                          0  ...                    0                   1   
1                          0  ...                    0                   1   
2                          0  ...                    0                   1   
3                          0  ...                    0                   1   
4                          1  ...                    0                   1   
...                      ...  ...                  ...                 ...   
10495                      1  ...                    0                   1   
10496                      1  ...                    0                   1   
10497                      1  ...                    0                   1   
10498                      1  ...                    0                   1   
10499                      0  ...                    1                   0   

       Merchant_ID_Sekunder  Country_ID_Asing  Country_ID_Indonesia  \
0                         0    

Melihat informasi dasar dari dataframe yang memiliki dummy variable.

In [36]:
df2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 10484 entries, 0 to 10499
Data columns (total 26 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   Transaction_Amount             10484 non-null  float64
 1   Average_Transaction_Amount     10484 non-null  float64
 2   Maximum_Transaction_Amount     10484 non-null  float64
 3   Minimum_Transaction_Amount     10484 non-null  float64
 4   Average_Transaction_Frequency  10484 non-null  float64
 5   Fraud_Status                   10484 non-null  int64  
 6   Range                          10484 non-null  float64
 7   Transaction_Type_Jarang        10484 non-null  uint8  
 8   Transaction_Type_Sering        10484 non-null  uint8  
 9   Transaction_Type_Umum          10484 non-null  uint8  
 10  Card_Type_Gold                 10484 non-null  uint8  
 11  Card_Type_Platinum             10484 non-null  uint8  
 12  Card_Type_Silver               10484 non-null 

# EDA

#### Pada tahap ini, kami melakukan Exploratory Data Analysis.

Tahap pertama adalah Profiling. Tahapan ini dilakukan untuk melihat kembali setiap kolom pada dataframe yang sudah final.

In [37]:
profile = ProfileReport(df2, title="Pandas Profiling Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Memunculkan Descriptive Statistics dari data final.

In [38]:
df2.describe()

Transaction_Amount  Average_Transaction_Amount  \
count        1.048400e+04                1.048400e+04   
mean         1.319614e+06                1.366425e+06   
std          2.818545e+06                1.439952e+06   
min          1.000000e+00                5.000000e+04   
25%          2.000000e+05                5.708772e+05   
50%          5.800000e+05                1.026553e+06   
75%          1.250000e+06                1.691944e+06   
max          6.000000e+07                2.466667e+07   

       Maximum_Transaction_Amount  Minimum_Transaction_Amount  \
count                1.048400e+04                1.048400e+04   
mean                 1.229132e+07                7.735985e+04   
std                  1.640702e+07                7.496893e+05   
min                  3.800000e+04                1.000000e+00   
25%                  2.500000e+06                2.500000e+04   
50%                  6.000000e+06                3.750000e+04   
75%                  1.500000e+07                6.550000e+04   
max                  1.000000e+08                7.500000e+07   

       Average_Transaction_Frequency  Fraud_Status         Range  \
count                   10484.000000  10484.000000  1.048400e+04   
mean                        2.435969      0.068104  1.221396e+07   
std                         1.390293      0.251936  1.638476e+07   
min                         1.000000      0.000000 -1.500000e+06   
25%                         1.680000      0.000000  2.471075e+06   
50%                         2.100000      0.000000  5.976675e+06   
75%                         2.780000      0.000000  1.490000e+07   
max                        19.780000      1.000000  9.998000e+07   

       Transaction_Type_Jarang  Transaction_Type_Sering  \
count             10484.000000             10484.000000   
mean                  0.023178                 0.735216   
std                   0.150476                 0.441239   
min                   0.000000                 0.000000   
25%                   0.000000                 0.000000   
50%                   0.000000                 1.000000   
75%                   0.000000                 1.000000   
max                   1.000000                 1.000000   

       Transaction_Type_Umum  ...  Channel_ID_Sekunder  Merchant_ID_Primer  \
count           10484.000000  ...         10484.000000        10484.000000   
mean                0.241606  ...             0.207173            0.860549   
std                 0.428077  ...             0.405300            0.346433   
min                 0.000000  ...             0.000000            0.000000   
25%                 0.000000  ...             0.000000            1.000000   
50%                 0.000000  ...             0.000000            1.000000   
75%                 0.000000  ...             0.000000            1.000000   
max                 1.000000  ...             1.000000            1.000000   

       Merchant_ID_Sekunder  Country_ID_Asing  Country_ID_Indonesia  \
count          10484.000000      10484.000000          10484.000000   
mean               0.139451          0.003434              0.996566   
std                0.346433          0.058501              0.058501   
min                0.000000          0.000000              0.000000   
25%                0.000000          0.000000              1.000000   
50%                0.000000          0.000000              1.000000   
75%                0.000000          0.000000              1.000000   
max                1.000000          1.000000              1.000000   

       EDC_Type_Bank  EDC_Type_GPRS  EDC_Type_Mobile  EDC_Owner_Pemilik  \
count   10484.000000   10484.000000     10484.000000       10484.000000   
mean        0.067245       0.897940         0.034815           0.792827   
std         0.250458       0.302742         0.183320           0.405300   
min         0.000000       0.000000         0.000000           0.000000   
25%         0.000000       1.000000         

## Define Predictors and Target Variable

Pada tahap ini, kami mulai menentukan variabel yang akan digunakan sebagai Predictor (variabel yang digunakan untuk memprediksi) dan Target (variabel yang akan diprediksi).

In [39]:
TargetVariable = 'Fraud_Status'
Predictors = ['Transaction_Amount',
              'Average_Transaction_Amount',
              'Minimum_Transaction_Amount',
              'Average_Transaction_Frequency',
              'Transaction_Type_Jarang',
              'Transaction_Type_Sering',
              'Transaction_Type_Umum',
              'Merchant_ID_Primer',
              'Merchant_ID_Sekunder',
              'Country_ID_Asing',
              'Country_ID_Indonesia',
              'EDC_Type_Bank',
              'EDC_Type_GPRS',
              'EDC_Type_Mobile',
              'EDC_Owner_Pemilik',
              'EDC_Owner_Sewa',
              'Range']

In [41]:
X=df2[Predictors]
y=df2[TargetVariable]

# Model Without H2O

#### Pertama, kami akan mencoba berbagai model tanpa menggunakan H2O.

Train-Test Split akan dilakukan untuk tahap ini. Test size akan diambil 30%, serta random state ditentukan agar pada saat program dijalankan datanya akan tetap sama (tidak di-random ulang).

In [42]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=101)

## Logistic Regression

Melakukan fitting model logistic regression dengan parameter default terhadap data train.

In [43]:
logmodel = LogisticRegression()
logmodel.fit(X_train,y_train)

LogisticRegression()

Melakukan prediksi dengan memasukkan nilai predictor dari test menggunakan model Logistic Regression yang sudah fit. Setelah itu, kami menampilkan nilai classification report untuk melihat keakuratan prediksi. Dari classification report di bawah, terlihat bahwa f1 untuk nilai 0 sangat tinggi, sedangkan untuk nilai 1 sangat rendah. Ini artinya model ini kurang baik. Hal ini dapat terjadi karena perbedaan antara jumlah 0 dan 1 sangat jauh.

In [44]:
predictions = logmodel.predict(X_test)
print(classification_report(y_test, predictions))

              precision    recall  f1-score   support

           0       0.93      1.00      0.96      2930
           1       0.25      0.01      0.02       216

    accuracy                           0.93      3146
   macro avg       0.59      0.50      0.49      3146
weighted avg       0.88      0.93      0.90      3146



Selanjutnya, kami menampilkan nilai nilai akurasi dan f1 dengan menggunakan 10-Fold Cross-Validation, dengan 9 bagian dari data akan dijadikan data train, serta 1 bagian dari data akan dijadikan data test. Kemudian, hasil prediksi dengan data train akan dibandingkan dengan nilai dari data test tersebut. Ini akan dilakukan 10 kali dengan bagian data yang berbeda.

In [45]:
Accuracy_Values_log=cross_val_score(logmodel, X , y, cv=10)
print('\nAccuracy values for 10-fold Cross Validation:\n',Accuracy_Values_log)
print('\nFinal Average Accuracy of the model:', round(Accuracy_Values_log.mean(),3))

f1results_log=cross_val_score(logmodel,X,y,cv=10,scoring='f1')
print ('F1 score for 10-fold Cross Validation:\n',f1results_log)
print('\nFinal Average F1 Score of the model:', round(f1results_log.mean(),3))


Accuracy values for 10-fold Cross Validation:
 [0.9313632  0.93326978 0.93231649 0.9313632  0.93034351 0.93320611
 0.93129771 0.93034351 0.93034351 0.93225191]

Final Average Accuracy of the model: 0.932
F1 score for 10-fold Cross Validation:
 [0.         0.05405405 0.02739726 0.02702703 0.         0.05405405
 0.07692308 0.         0.         0.        ]

Final Average F1 Score of the model: 0.024


Hasil nilai akurasi dan f1 tidak berbeda jauh, sehingga model ini memang terbukti tidak terlalu baik.

## Decision Tree

Selanjutnya kami melakukan fitting model Decision Tree. Model Decision Tree ini menggunakan parameter max_depth=8 dan criterion entropy. Parameter ini dipilih menggunakan metode Trial and Error dan Grid Search Cross Validation (Tidak ditampilkan di sini karena running program tersebut terlalu lama).

In [46]:
model1 = DecisionTreeClassifier(max_depth=8,criterion='entropy')
model1.fit(X_train,y_train)

DecisionTreeClassifier(criterion='entropy', max_depth=8)

Melakukan prediksi menggunakan model Decision Tree yang sudah fit, lalu menampilkan Classification Report. Dari sini terlihat bahwa nilai akurasi di 0.93 dan f1 juga masih berbeda cukup jauh, namun f1 untuk 1 tidak sekecil pada model sebelumnya.

In [47]:
y_prediksi = model1.predict(X_test)
print(classification_report(y_test,y_prediksi))

              precision    recall  f1-score   support

           0       0.95      0.98      0.97      2930
           1       0.54      0.25      0.34       216

    accuracy                           0.93      3146
   macro avg       0.74      0.62      0.65      3146
weighted avg       0.92      0.93      0.92      3146



Selanjutnya kami juga menampilkan nilai akurasi dan f1 dari 10-Fold Cross-Validation. Hasilnya sudah mencapai 0.937 untuk akurasi dan 0.401 untuk f1. Sudah meningkat drastis.

In [48]:
Accuracy_Values_DT=cross_val_score(model1, X , y, cv=10)
print('\nAccuracy values for 10-fold Cross Validation:\n',Accuracy_Values_DT)
print('\nFinal Average Accuracy of the model:', round(Accuracy_Values_DT.mean(),3))

f1results_DT=cross_val_score(model1,X,y,cv=10,scoring='f1')
print ('F1 score for 10-fold Cross Validation:\n',f1results_DT)
print('\nFinal Average F1 Score of the model:', round(f1results_DT.mean(),3))


Accuracy values for 10-fold Cross Validation:
 [0.92183031 0.93803622 0.92850334 0.93803622 0.9360687  0.9379771
 0.9351145  0.94465649 0.94942748 0.94370229]

Final Average Accuracy of the model: 0.937
F1 score for 10-fold Cross Validation:
 [0.30508475 0.3963964  0.31775701 0.40366972 0.34285714 0.45378151
 0.42735043 0.43396226 0.51376147 0.41904762]

Final Average F1 Score of the model: 0.401


## Random Forest

Model selanjutnya adalah Random Forest. Model ini adalah pengembangan lebih lanjut dari Decision Tree. Parameter yang digunakan untuk Random Forest adalah max_depth=14, criterion=entropy, dan n_estimators=7.

In [49]:
rfc = RandomForestClassifier(max_depth=14,criterion='entropy',n_estimators=7)
rfc.fit(X_train, y_train)

RandomForestClassifier(criterion='entropy', max_depth=14, n_estimators=7)

Hasil classification report ini lebih buruk dari milik decision tree.

In [50]:
rfc_pred = rfc.predict(X_test)
print(classification_report(y_test,rfc_pred))

              precision    recall  f1-score   support

           0       0.95      0.99      0.97      2930
           1       0.57      0.25      0.35       216

    accuracy                           0.94      3146
   macro avg       0.76      0.62      0.66      3146
weighted avg       0.92      0.94      0.92      3146



Hasil dari 10-Fold Cross Validation juga lebih buruk daripada Decision Tree. Artinya, model ini kurang bagus untuk data ini. Alasan lain yang mungkin adalah pemilihan parameter yang tepat. Namun, pemilihan parameter sangat sulit dilakukan karena program random forest yang dijalankan sangat lama.

In [51]:
Accuracy_Values_RF=cross_val_score(rfc, X , y, cv=10)
print('\nAccuracy values for 10-fold Cross Validation:\n',Accuracy_Values_RF)
print('\nFinal Average Accuracy of the model:', round(Accuracy_Values_RF.mean(),3))

f1results_RF=cross_val_score(rfc,X,y,cv=10,scoring='f1')
print ('F1 score for 10-fold Cross Validation:\n',f1results_RF)
print('\nFinal Average F1 Score of the model:', round(f1results_RF.mean(),3))


Accuracy values for 10-fold Cross Validation:
 [0.93422307 0.94089609 0.93326978 0.93040991 0.93416031 0.93225191
 0.9370229  0.94465649 0.94465649 0.9398855 ]

Final Average Accuracy of the model: 0.937
F1 score for 10-fold Cross Validation:
 [0.31067961 0.39252336 0.21276596 0.27722772 0.42307692 0.34951456
 0.3853211  0.36893204 0.38834951 0.27956989]

Final Average F1 Score of the model: 0.339


## AdaBoost

Model selanjutnya adalah AdaBoost. Model ini menggunakan base estimator decision tree yang sama dengan decision tree di atas. Jumlah estimator yang dipilih adalah 2 dan learning ratenya adalah 0.07. 

In [52]:
DTR = DecisionTreeClassifier(max_depth=8,criterion='entropy')
RegModel= AdaBoostClassifier(n_estimators=2, base_estimator=DTR ,learning_rate=0.07)

Hasil Classification Report juga menunjukkan hasil yang mirip seperti Decision Tree, namun sedikit lebih bagus.

In [53]:
AB=RegModel.fit(X_train,y_train)
ABprediction=AB.predict(X_test)
print(classification_report(y_test,rfc_pred))

              precision    recall  f1-score   support

           0       0.95      0.99      0.97      2930
           1       0.57      0.25      0.35       216

    accuracy                           0.94      3146
   macro avg       0.76      0.62      0.66      3146
weighted avg       0.92      0.94      0.92      3146



Selanjutnya, kami melakukan 10-Fold Cross Validation untuk melihat hasil akurasi dan f1. Hasilnya juga tidak jauh berbeda dari hasil classification report. F1 yang didapat juga lebih tinggi dari hasil decision tree.

In [54]:
Accuracy_Values_AB=cross_val_score(RegModel, X , y, cv=10)
print('\nAccuracy values for 10-fold Cross Validation:\n',Accuracy_Values_AB)
print('\nFinal Average Accuracy of the model:', round(Accuracy_Values_AB.mean(),3))

f1results_AB=cross_val_score(RegModel,X,y,cv=10,scoring='f1')
print ('F1 score for 10-fold Cross Validation:\n',f1results_AB)
print('\nFinal Average F1 Score of the model:', round(f1results_AB.mean(),3))


Accuracy values for 10-fold Cross Validation:
 [0.92755005 0.93040991 0.93231649 0.93231649 0.9351145  0.94083969
 0.9360687  0.9389313  0.94847328 0.94465649]

Final Average Accuracy of the model: 0.937
F1 score for 10-fold Cross Validation:
 [0.24074074 0.36363636 0.33009709 0.3364486  0.43243243 0.46956522
 0.39285714 0.38888889 0.44444444 0.39175258]

Final Average F1 Score of the model: 0.379


Berikut ini merupakan semua hasil akurasi dan f1 dari keempat model di atas yang ditampilkan dalam sebuah tabel. Dari tabel ini, sudah jelas terlihat bahwa AdaBoost memiliki f1 yang paling tinggi, sedangkan nilai akurasi semuanya tidak berbeda jauh.

In [55]:
metrics = ['Accuracy', 'F1 Score']
performance_Linear_Regression = [round(Accuracy_Values_log.mean(),3), round(f1results_log.mean(),3)]
performance_Decision_Tree=[round(Accuracy_Values_DT.mean(),3), round(f1results_DT.mean(),3)]
performance_Random_Forest=[round(Accuracy_Values_RF.mean(),3), round(f1results_RF.mean(),3)]
performance_AdaBoost=[round(Accuracy_Values_AB.mean(),3), round(f1results_AB.mean(),3)]

In [56]:
performance1 = pd.DataFrame({'Metrics': metrics, 'Performance_Linear_Regression': performance_Linear_Regression, 'Performace_Decision_Tree':performance_Decision_Tree, 'Performance_Random_Forest':performance_Random_Forest, 'Performance_AdaBoost':performance_AdaBoost})
performance1

Metrics  Performance_Linear_Regression  Performace_Decision_Tree  \
0  Accuracy                          0.932                     0.937   
1  F1 Score                          0.024                     0.401   

   Performance_Random_Forest  Performance_AdaBoost  
0                      0.937                 0.937  
1                      0.339                 0.379

# Model With H20

Melakukan train-test split dengan parameter stratified, dimana pada data kategori, penggunaan parameter ini akan menjaga proporsi data 0 dan 1 dari target variable tetap sama pada data yang sudah di-split dengan data sebenarnya yang digunakan. Train-test split dijalankan sebanyak 30 kali, dimana data train dan test pada masing-masing iterasi akan disimpan dalam list.

In [57]:
start_time = pd.to_datetime('now') + pd.Timedelta('07:00:00')
trains = []
tests = []

for i in range(0,30):
    
    train, test = train_test_split(df2, test_size=0.3, stratify=df2[TargetVariable])
    train = h2o.H2OFrame(train)
    test = h2o.H2OFrame(test)
    train[TargetVariable] = train[TargetVariable].asfactor()
    test[TargetVariable] = test[TargetVariable].asfactor()
    trains.append(train)
    tests.append(test)

timer(start_time, header='\nConverting DataFrame to H2O Frame')

/opt/anaconda3/lib/python3.9/site-packages/pandas/core/arrays/datetimes.py:2199: FutureWarning: The parsing of 'now' in pd.to_datetime without `utc=True` is deprecated. In a future version, this will match Timestamp('now') and Timestamp.now()
  result, tz_parsed = tslib.array_to_datetime(


Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |█████████████████████████████████

/opt/anaconda3/lib/python3.9/site-packages/pandas/core/arrays/datetimes.py:2199: FutureWarning: The parsing of 'now' in pd.to_datetime without `utc=True` is deprecated. In a future version, this will match Timestamp('now') and Timestamp.now()
  result, tz_parsed = tslib.array_to_datetime(


## Random Forest

Setelah itu, kami menggunakan model random forest dari H2O. Random Forest ini sudah mengikuti parameter default dari H2O. Fitting model random forest dilakukan 30 kali untuk 30 hasil train-test split yang berbeda.

In [58]:
model_RF=[]
for i in range (30):
    rf = H2ORandomForestEstimator()
    rf.train(x=Predictors, y=TargetVariable, training_frame=trains[i], validation_frame=tests[i])
    model_RF.append(rf)

drf Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
drf Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
drf Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
drf Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
drf Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
drf Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
drf Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
drf Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
drf Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
drf Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
drf Model Build progress: |███████████████████████

### F1, Precision, Sensitivity, Accuracy with Random Forest

Kami juga melihat hasil prediksi model ini dengan menggunakan f1, threshold, precision, sensitivity, dan accuracy. Meski begitu, yang akan dilihat secara khusus adalah f1. Hasil yang ditampilkan di bawah adalah mean dan standard deviation dari 30 hasil train-test split tersebut. Hasil mean f1 ini sudah lebih bagus dari semua model sebelum H2O. Hal ini dapat terjadi dikarenakan train-test split sudah menggunakan stratified.

In [60]:
mean=[]
std=[]
f1_total=[]
threshold_total=[]
precision_total=[]
sensitivity_total=[]
accuracy_total=[]
var=[]

for i in range (30):
    f1 = model_RF[i].F1(valid=True)[0][1]
    f1_total.append(f1)
    threshold = model_RF[i].F1(valid=True)[0][0]
    threshold_total.append(threshold)
    precision = model_RF[i].precision(train=False,valid=True,xval=False,thresholds=threshold)[0][1]
    precision_total.append(precision)
    sensitivity = model_RF[i].sensitivity(train=False,valid=True,xval=False,thresholds=threshold)[0][1]
    sensitivity_total.append(sensitivity)
    accuracy = model_RF[i].accuracy(train=False,valid=True,xval=False,thresholds=threshold)[0][1]
    accuracy_total.append(accuracy)
    vars = model_RF[i].varimp(use_pandas=True)
    var.append(vars)

parameter = [f1_total,threshold_total,precision_total,sensitivity_total,accuracy_total]

for i in range(len(parameter)):
    mean.append(np.mean(parameter[i]))
    std.append(np.std(parameter[i]))

random_forest = pd.DataFrame({'parameter':['F1','Threshold','Precision','Sensitivity','Accuracy'],'mean':mean, 'std':std})
random_forest

parameter      mean       std
0           F1  0.440283  0.019126
1    Threshold  0.278369  0.038712
2    Precision  0.436515  0.043549
3  Sensitivity  0.449844  0.035709
4     Accuracy  0.922049  0.007701

## Gradient Boosting

Selanjutnya, kami menggunakan model Gradient Boosting dari H2O. Sama seperti Random Forest sebelumnya, Gradient Boosting ini juga sudah mengikuti parameter default dari H2O. Fitting model Gradient Boosting dilakukan 30 kali untuk 30 hasil train-test split yang berbeda.

In [61]:
model_GB=[]
for i in range (30):
    gb = H2OGradientBoostingEstimator()
    gb.train(x=Predictors, y=TargetVariable, training_frame=trains[i], validation_frame=tests[i])
    model_GB.append(gb)

gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |██████████████████████████████████████████████████████| (done) 100%
gbm Model Build progress: |███████████████████████

### Predict

Berikut adalah hasil prediksi dengan menggunakan Gradient Boosting.

In [62]:
gb.predict(test)

gbm prediction progress: |███████████████████████████████████████████████████████| (done) 100%


predict p0 p1 
 
 
 0 0.978468 0.0215318 
 0 0.948953 0.051047 
 0 0.978309 0.0216914 
 0 0.932361 0.0676388 
 1 0.345128 0.654872 
 0 0.977582 0.0224181 
 0 0.935669 0.0643312 
 0 0.96792 0.0320799 
 0 0.965627 0.0343734 
 0 0.925226 0.0747737

### F1, Precision, Sensitivity, Accuracy with Gradient Boosting

Kami juga melihat hasil prediksi model ini dengan menggunakan f1, threshold, precision, sensitivity, dan accuracy terhadap model ini. Sama seperti sebelumnya, hasil yang dilihat adalah f1. Hasil yang ditampilkan di bawah adalah mean dan standard deviation dari 30 hasil train-test split tersebut. Kami juga melihat hasil prediksi model ini dengan menggunakan f1, threshold, precision, sensitivity, dan accuracy. Hasil mean f1 ini bahkan lebih bagus dari model Random Forest H2O.

In [80]:
mean=[]
std=[]
f1_total=[]
threshold_total=[]
precision_total=[]
sensitivity_total=[]
accuracy_total=[]
var=[]

for i in range (30):
    f1 = model_GB[i].F1(valid=True)[0][1]
    f1_total.append(f1)
    threshold = model_GB[i].F1(valid=True)[0][0]
    threshold_total.append(threshold)
    precision = model_GB[i].precision(train=False,valid=True,xval=False,thresholds=threshold)[0][1]
    precision_total.append(precision)
    sensitivity = model_GB[i].sensitivity(train=False,valid=True,xval=False,thresholds=threshold)[0][1]
    sensitivity_total.append(sensitivity)
    accuracy = model_GB[i].accuracy(train=False,valid=True,xval=False,thresholds=threshold)[0][1]
    accuracy_total.append(accuracy)
    vars = model_GB[i].varimp(use_pandas=True)
    var.append(vars)

parameter=[f1_total,threshold_total,precision_total,sensitivity_total,accuracy_total]

for i in range(len(parameter)):
    mean.append(np.mean(parameter[i]))
    std.append(np.std(parameter[i]))

gradientboosting=pd.DataFrame({'parameter':['F1','Threshold','Precision','Sensitivity','Accuracy'],'mean':mean, 'std':std})
gradientboosting

parameter      mean       std
0           F1  0.481085  0.022416
1    Threshold  0.228197  0.050591
2    Precision  0.502268  0.049518
3  Sensitivity  0.468536  0.046930
4     Accuracy  0.931235  0.006913

# Predict Model to Data Testing

## Importing Data Testing and Dropping Useless Columns

Hal pertama yang kami lakukan sama seperti saat melakukan importing pada data training, yaitu kami mengimport data yang akan digunakan. Kami langsung menghilangkan nan pada data ini karena proporsi nan di data ini sangat kecil dibandingkan keseluruhan datanya. Selain itu, kolom Transaction_ID di-drop karena setiap row unik, Transaction_Flag di-drop karena semuanya sama, dan Bank_ID juga di-drop karena semuanya juga sama. Dropna dan drop kolom menggunakan True pada parameter inplace agar modifikasi tersebut langsung dilakukan pada dataframe tersebut tanpa membuat dataframe baru.

In [81]:
dft = pd.read_excel('cctx_test.xlsx')
dft.dropna(inplace=True)
dft.drop(['Transaction_Flag', 'Bank_ID'], axis=1, inplace=True)
dft

Transaction_ID        Transaction_Date Transaction_Type  \
0           TX00001 2018-01-01 01:48:50.951              T13   
1           TX00003 2018-01-01 01:48:50.951              T01   
2           TX00011 2018-01-02 12:05:24.232              T15   
3           TX00012 2018-01-02 12:49:24.403              T06   
4           TX00013 2018-01-02 15:22:15.525              T15   
...             ...                     ...              ...   
2620        TX13111 2018-12-31 10:18:30.622              T03   
2621        TX13112 2018-12-31 10:32:42.888              T15   
2622        TX13115 2018-12-31 13:49:12.566              T15   
2623        TX13119 2018-12-31 15:47:34.782              T13   
2624        TX13120 2018-12-31 15:47:34.782              T13   

      Transaction_Amount     CC_ID Card_Type  Card_Holder  Channel_ID  \
0                 250000  CCID6063      CC12            2           1   
1                  50000  CCID5738      CC10            2           1   
2                1000000  CCID4708      CC11            2           1   
3                1200000  CCID7183      CC10            1           5   
4                1000000  CCID1248      CC08            2           1   
...                  ...       ...       ...          ...         ...   
2620             1500000  CCID4922      CC08            2           1   
2621              100000  CCID1508      CC11            2           1   
2622             1100000  CCID5731      CC11            2           1   
2623             2050000  CCID6497      CC08            2           1   
2624             1000000  CCID5547      CC09            2           1   

     Merchant_ID Country_ID    City_ID EDC_Type EDC_Location EDC_Owner  \
0          M0001      CTY06  CTY06-133  EDC3501     LEDC3933  OEDC0377   
1          M0001      CTY06  CTY06-133  EDC2427     LEDC1692  OEDC0377   
2          M0001      CTY06  CTY06-013  EDC1912     LEDC1223  OEDC0377   
3          M0001      CTY06  CTY06-073  EDC0002     LEDC3986  OEDC0638   
4          M0001      CTY06  CTY06-181  EDC3485     LEDC2427  OEDC0377   
...          ...        ...        ...      ...          ...       ...   
2620       M0001      CTY06  CTY06-133  EDC1055     LEDC0293  OEDC0377   
2621       M0001      CTY06  CTY06-133  EDC2515     LEDC1739  OEDC0377   
2622       M0001      CTY06  CTY06-171  EDC1653     LEDC0925  OEDC0377   
2623       M0001      CTY06  CTY06-023  EDC0494     LEDC3750  OEDC0377   
2624       M0001      CTY06  CTY06-023  EDC0738     LEDC3806  OEDC0377   

      Average_Transaction_Amount  Maximum_Transaction_Amount  \
0                      444720.76                   2300000.0   
1                      102718.18                    500000.0   
2                     1388235.29                   7000000.0   
3                     1361486.42                   5000000.0   
4                     4143191.19                  99000000.0   
...                          ...                         ...   
2620                   895194.18                  10000000.0   
2621                   857803.65                   4200000.0   
2622                   904045.87                   9500000.0   
2623                  4906702.85                  75000000.0   
2624                   617486.59                   3000000.0   

      Minimum_Transaction_Amount  Average_Transaction_Frequency  
0                        28900.0                           1.53  
1                        50000.0                           1.47  
2                        30000.0                           2.60  
3                        26500.0                           2.56  
4                        25000.0                           3.05  
...                          ...                            ...  
2620                     47500.0                           1.90  
2621                    100000.0                           2.18  
2622                     20800.0                           2.57  
2623                    100000.0         

Kemudian kami ingin melihat bentuk data testing kami.

In [82]:
dft.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2620 entries, 0 to 2624
Data columns (total 18 columns):
 #   Column                         Non-Null Count  Dtype         
---  ------                         --------------  -----         
 0   Transaction_ID                 2620 non-null   object        
 1   Transaction_Date               2620 non-null   datetime64[ns]
 2   Transaction_Type               2620 non-null   object        
 3   Transaction_Amount             2620 non-null   int64         
 4   CC_ID                          2620 non-null   object        
 5   Card_Type                      2620 non-null   object        
 6   Card_Holder                    2620 non-null   int64         
 7   Channel_ID                     2620 non-null   int64         
 8   Merchant_ID                    2620 non-null   object        
 9   Country_ID                     2620 non-null   object        
 10  City_ID                        2620 non-null   object        
 11  EDC_Type         

# Binning Data Test

Sama halnya ketika melakukan assign pada binning data training, fungsi  assign ini digunakan untuk mengganti suatu nilai berdasarkan kondisi tertentu. Kondisi dapat ditetapkan sendiri atau dengan menentukan rentang jumlah. Jika nilai tertentu dalam suatu kolom memiliki jumlah di antara nilai yang ditentukan. Misalnya, huruf a hanya ada satu, sedangkan jumlah yang diinginkan adalah minimal 5. Maka dengan menggunakan fungsi ini, a dapat diganti dengan nilai yang diinginkan. Fungsi ini berguna untuk melakukan binning terhadap nilai atau kategori yang jumlahnya hanya sedikit

Dalam menetapkan kondisi, kami akan menyamakan kondisi yang sudah dibuat pada data training untuk kondisi binning pada data testing.

In [83]:
assign(dft, 'Country_ID', False, ['Indonesia', 'Asing'], con=con_Country_ID, ret=False)

assign(dft, 'EDC_Type', False, ['Bank', 'Mobile', 'GPRS'], con=con_EDC_Type, ret=False)

assign(dft, 'EDC_Owner',False, ['Pemilik', 'Sewa'], con=con_EDC_Owner, ret=False)

assign(dft, 'Transaction_Type', False, ['Sering', 'Umum', 'Jarang'], con=con_Transaction_Type, ret=False)

assign(dft, 'Card_Type', False, ['Platinum', 'Gold', 'Silver'], con=con_Card_Type, ret=False)

assign(dft, 'Channel_ID', False, ['Primer', 'Sekunder'], con=con_Channel_ID, ret=False)

assign(dft, 'Merchant_ID', False, ['Primer', 'Sekunder'], con=con_Merchant_ID, ret=False)

dft.loc[dft[dft['Card_Holder'] == 2].index, 'Card_Holder'] = 'Primer'
dft.loc[dft[dft['Card_Holder'] == 1].index, 'Card_Holder'] = 'Sekunder'
dft['Card_Holder'] = dft['Card_Holder'].astype('category')
dft.info()

Column: Country_ID
Indonesia    2612
Asing           6
CTY03           1
CTY11           1
Name: Country_ID, dtype: int64
Column: EDC_Type
GPRS       1740
Bank        175
Mobile       84
EDC4519       3
EDC0153       3
           ... 
EDC1878       1
EDC2569       1
EDC4576       1
EDC0440       1
EDC2515       1
Name: EDC_Type, Length: 554, dtype: int64
Column: EDC_Owner
Pemilik     2089
Sewa         305
OEDC1002       3
OEDC1506       3
OEDC0050       2
            ... 
OEDC1628       1
OEDC0608       1
OEDC0076       1
OEDC0480       1
OEDC0744       1
Name: EDC_Owner, Length: 207, dtype: int64
Column: Transaction_Type
Sering    1915
Umum       651
Jarang      54
Name: Transaction_Type, dtype: int64
Column: Card_Type
Gold        1968
Platinum     587
Silver        65
Name: Card_Type, dtype: int64
Column: Channel_ID
Primer      2089
Sekunder     531
Name: Channel_ID, dtype: int64
Column: Merchant_ID
Primer      2265
Sekunder     201
M0935          2
M0380          2
M0695          2


Binning dilakukan berdasarkan kondisi pertama yang sudah dilakukan pada data train sebelumnya. Setelah itu, dilakukan binning terhadap data yang baru muncul pada data test. Karena data tersebut baru ada, maka belum termasuk ke data binning sebelumnya. Sehingga binning kedua dilakukan untuk data yang baru.

In [84]:
col = 'Country_ID'
ran = [0, 2_000, 3_000]
val = ['Indonesia', 'Asing']
assign(dft, col, ran, val, ret=False)

col = 'EDC_Type'
ran = [0, 10, 100, 200, 2_000]
val = ['GPRS', 'Mobile', 'Bank', 'GPRS']
assign(dft, col, ran, val, ret=False)

col = 'EDC_Owner'
ran = [0, 400, 3_000]
val = ['Sewa', 'Pemilik']
assign(dft, col, ran, val, ret=False)

col = 'Merchant_ID'
ran = [0, 300, 3_000]
val = ['Primer', 'Sekunder']
assign(dft, col, ran, val, ret=False)

Column: Country_ID
2612	replaced by Indonesia	with condition 2000 < value_counts <= 3000
8	replaced by Asing	with condition 0    < value_counts <= 2000
Indonesia    2612
Asing           8
CTY03           0
CTY11           0
Name: Country_ID, dtype: int64
Column: EDC_Type
1740	replaced by GPRS	with condition 200  < value_counts <= 2000
175	replaced by Mobile	with condition 100  < value_counts <= 200
259	replaced by Bank	with condition 10   < value_counts <= 100
621	replaced by GPRS	with condition 0    < value_counts <= 10
GPRS       2361
Bank        259
EDC3628       0
EDC3558       0
EDC3576       0
           ... 
EDC1842       0
EDC1837       0
EDC1832       0
EDC1830       0
Mobile        0
Name: EDC_Type, Length: 554, dtype: int64
Column: EDC_Owner
2089	replaced by Sewa	with condition 400  < value_counts <= 3000
2620	replaced by Pemilik	with condition 0    < value_counts <= 400
Pemilik     2620
OEDC0002       0
OEDC1155       0
OEDC1060       0
OEDC1071       0
            ... 
OED

In [117]:
dft['Card_Holder'].value_counts()

Primer      2444
Sekunder     176
Name: Card_Holder, dtype: int64

In [85]:
dft['Range'] = dft['Maximum_Transaction_Amount'] - dft['Minimum_Transaction_Amount']

In [86]:
dft2 = pd.get_dummies(dft.drop(['Transaction_Date', 'CC_ID', 'EDC_Location','City_ID'], axis=1))

In [87]:
dft2

Transaction_Amount  Average_Transaction_Amount  \
0                 250000                   444720.76   
1                  50000                   102718.18   
2                1000000                  1388235.29   
3                1200000                  1361486.42   
4                1000000                  4143191.19   
...                  ...                         ...   
2620             1500000                   895194.18   
2621              100000                   857803.65   
2622             1100000                   904045.87   
2623             2050000                  4906702.85   
2624             1000000                   617486.59   

      Maximum_Transaction_Amount  Minimum_Transaction_Amount  \
0                      2300000.0                     28900.0   
1                       500000.0                     50000.0   
2                      7000000.0                     30000.0   
3                      5000000.0                     26500.0   
4                     99000000.0                     25000.0   
...                          ...                         ...   
2620                  10000000.0                     47500.0   
2621                   4200000.0                    100000.0   
2622                   9500000.0                     20800.0   
2623                  75000000.0                    100000.0   
2624                   3000000.0                    100000.0   

      Average_Transaction_Frequency       Range  Transaction_ID_TX00001  \
0                              1.53   2271100.0                       1   
1                              1.47    450000.0                       0   
2                              2.60   6970000.0                       0   
3                              2.56   4973500.0                       0   
4                              3.05  98975000.0                       0   
...                             ...         ...                     ...   
2620                           1.90   9952500.0                       0   
2621                           2.18   4100000.0                       0   
2622                           2.57   9479200.0                       0   
2623                           2.91  74900000.0                       0   
2624                           1.67   2900000.0                       0   

      Transaction_ID_TX00003  Transaction_ID_TX00011  Transaction_ID_TX00012  \
0                          0                       0                       0   
1                          1                       0                       0   
2                          0                       1                       0   
3                          0                       0                       1   
4                          0                       0                       0   
...                      ...                     ...                     ...   
2620                       0                       0                       0   
2621                       0                       0                       0   
2622                       0                       0                       0   
2623                       0                       0                       0   
2624                       0                       0                       0   

      ...  EDC_Owner_OEDC1614  EDC_Owner_OEDC1622  EDC_Owner_OEDC1628  \
0     ...                   0                   0                   0   
1     ...                   0                   0                   0   
2     ...                   0                   0                   0   
3     ...                   0                   0                   0   
4     ...                   0                   0                   0   
...   ...                 ...                 ...                 ...   
2620  ...                   0                   0                   0   
2621  ...                   0                   0                   0   
2622  ...                   0                

# Prediction

In [88]:
X_dft=dft2[Predictors]

In [91]:
xdft = h2o.H2OFrame(X_dft)

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%


### Dalam melakukan prediksi, kami mengambil model pada indeks no 1

In [92]:
y_predicted = model_GB[1].predict(xdft)

gbm prediction progress: |███████████████████████████████████████████████████████| (done) 100%


In [93]:
dft.reset_index(inplace=True)
dft.drop('index',axis=1,inplace=True)

### Hasil dari prediksi dimasukkan ke dalam data index

In [94]:
dft['Fraud_Status']=h2o.as_list(y_predicted[0])
dft

Transaction_ID        Transaction_Date Transaction_Type  \
0           TX00001 2018-01-01 01:48:50.951             Umum   
1           TX00003 2018-01-01 01:48:50.951           Sering   
2           TX00011 2018-01-02 12:05:24.232           Sering   
3           TX00012 2018-01-02 12:49:24.403             Umum   
4           TX00013 2018-01-02 15:22:15.525           Sering   
...             ...                     ...              ...   
2615        TX13111 2018-12-31 10:18:30.622             Umum   
2616        TX13112 2018-12-31 10:32:42.888           Sering   
2617        TX13115 2018-12-31 13:49:12.566           Sering   
2618        TX13119 2018-12-31 15:47:34.782             Umum   
2619        TX13120 2018-12-31 15:47:34.782             Umum   

      Transaction_Amount     CC_ID Card_Type Card_Holder Channel_ID  \
0                 250000  CCID6063    Silver      Primer     Primer   
1                  50000  CCID5738      Gold      Primer     Primer   
2                1000000  CCID4708      Gold      Primer     Primer   
3                1200000  CCID7183      Gold    Sekunder   Sekunder   
4                1000000  CCID1248  Platinum      Primer     Primer   
...                  ...       ...       ...         ...        ...   
2615             1500000  CCID4922  Platinum      Primer     Primer   
2616              100000  CCID1508      Gold      Primer     Primer   
2617             1100000  CCID5731      Gold      Primer     Primer   
2618             2050000  CCID6497  Platinum      Primer     Primer   
2619             1000000  CCID5547      Gold      Primer     Primer   

     Merchant_ID Country_ID    City_ID EDC_Type EDC_Location EDC_Owner  \
0         Primer  Indonesia  CTY06-133     GPRS     LEDC3933   Pemilik   
1         Primer  Indonesia  CTY06-133     GPRS     LEDC1692   Pemilik   
2         Primer  Indonesia  CTY06-013     GPRS     LEDC1223   Pemilik   
3         Primer  Indonesia  CTY06-073     Bank     LEDC3986   Pemilik   
4         Primer  Indonesia  CTY06-181     GPRS     LEDC2427   Pemilik   
...          ...        ...        ...      ...          ...       ...   
2615      Primer  Indonesia  CTY06-133     GPRS     LEDC0293   Pemilik   
2616      Primer  Indonesia  CTY06-133     GPRS     LEDC1739   Pemilik   
2617      Primer  Indonesia  CTY06-171     GPRS     LEDC0925   Pemilik   
2618      Primer  Indonesia  CTY06-023     GPRS     LEDC3750   Pemilik   
2619      Primer  Indonesia  CTY06-023     GPRS     LEDC3806   Pemilik   

      Average_Transaction_Amount  Maximum_Transaction_Amount  \
0                      444720.76                   2300000.0   
1                      102718.18                    500000.0   
2                     1388235.29                   7000000.0   
3                     1361486.42                   5000000.0   
4                     4143191.19                  99000000.0   
...                          ...                         ...   
2615                   895194.18                  10000000.0   
2616                   857803.65                   4200000.0   
2617                   904045.87                   9500000.0   
2618                  4906702.85                  75000000.0   
2619                   617486.59                   3000000.0   

      Minimum_Transaction_Amount  Average_Transaction_Frequency       Range  \
0                        28900.0                           1.53   2271100.0   
1                        50000.0                           1.47    450000.0   
2                        30000.0                           2.60   6970000.0   
3                        26500.0                           2.56   4973500.0   
4                        25000.0                           3.05  98975000.0   
...                          ...                            ...         ...   
2615                     47500.0                           1.90   9952500.0   
2616                    100000.0                           2.18   4100000.0   
2617          

In [100]:
dft.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2620 entries, 0 to 2619
Data columns (total 20 columns):
 #   Column                         Non-Null Count  Dtype         
---  ------                         --------------  -----         
 0   Transaction_ID                 2620 non-null   object        
 1   Transaction_Date               2620 non-null   datetime64[ns]
 2   Transaction_Type               2620 non-null   category      
 3   Transaction_Amount             2620 non-null   int64         
 4   CC_ID                          2620 non-null   object        
 5   Card_Type                      2620 non-null   category      
 6   Card_Holder                    2620 non-null   category      
 7   Channel_ID                     2620 non-null   category      
 8   Merchant_ID                    2620 non-null   category      
 9   Country_ID                     2620 non-null   category      
 10  City_ID                        2620 non-null   object        
 11  EDC_Type         

# Fraud Status Prediction Result

In [115]:
dft[['Transaction_ID','Fraud_Status']]

Transaction_ID  Fraud_Status
0           TX00001             0
1           TX00003             0
2           TX00011             0
3           TX00012             1
4           TX00013             0
...             ...           ...
2615        TX13111             0
2616        TX13112             0
2617        TX13115             0
2618        TX13119             0
2619        TX13120             0

[2620 rows x 2 columns]

In [97]:
dft

Transaction_ID        Transaction_Date Transaction_Type  \
0           TX00001 2018-01-01 01:48:50.951             Umum   
1           TX00003 2018-01-01 01:48:50.951           Sering   
2           TX00011 2018-01-02 12:05:24.232           Sering   
3           TX00012 2018-01-02 12:49:24.403             Umum   
4           TX00013 2018-01-02 15:22:15.525           Sering   
...             ...                     ...              ...   
2615        TX13111 2018-12-31 10:18:30.622             Umum   
2616        TX13112 2018-12-31 10:32:42.888           Sering   
2617        TX13115 2018-12-31 13:49:12.566           Sering   
2618        TX13119 2018-12-31 15:47:34.782             Umum   
2619        TX13120 2018-12-31 15:47:34.782             Umum   

      Transaction_Amount     CC_ID Card_Type Card_Holder Channel_ID  \
0                 250000  CCID6063    Silver      Primer     Primer   
1                  50000  CCID5738      Gold      Primer     Primer   
2                1000000  CCID4708      Gold      Primer     Primer   
3                1200000  CCID7183      Gold    Sekunder   Sekunder   
4                1000000  CCID1248  Platinum      Primer     Primer   
...                  ...       ...       ...         ...        ...   
2615             1500000  CCID4922  Platinum      Primer     Primer   
2616              100000  CCID1508      Gold      Primer     Primer   
2617             1100000  CCID5731      Gold      Primer     Primer   
2618             2050000  CCID6497  Platinum      Primer     Primer   
2619             1000000  CCID5547      Gold      Primer     Primer   

     Merchant_ID Country_ID    City_ID EDC_Type EDC_Location EDC_Owner  \
0         Primer  Indonesia  CTY06-133     GPRS     LEDC3933   Pemilik   
1         Primer  Indonesia  CTY06-133     GPRS     LEDC1692   Pemilik   
2         Primer  Indonesia  CTY06-013     GPRS     LEDC1223   Pemilik   
3         Primer  Indonesia  CTY06-073     Bank     LEDC3986   Pemilik   
4         Primer  Indonesia  CTY06-181     GPRS     LEDC2427   Pemilik   
...          ...        ...        ...      ...          ...       ...   
2615      Primer  Indonesia  CTY06-133     GPRS     LEDC0293   Pemilik   
2616      Primer  Indonesia  CTY06-133     GPRS     LEDC1739   Pemilik   
2617      Primer  Indonesia  CTY06-171     GPRS     LEDC0925   Pemilik   
2618      Primer  Indonesia  CTY06-023     GPRS     LEDC3750   Pemilik   
2619      Primer  Indonesia  CTY06-023     GPRS     LEDC3806   Pemilik   

      Average_Transaction_Amount  Maximum_Transaction_Amount  \
0                      444720.76                   2300000.0   
1                      102718.18                    500000.0   
2                     1388235.29                   7000000.0   
3                     1361486.42                   5000000.0   
4                     4143191.19                  99000000.0   
...                          ...                         ...   
2615                   895194.18                  10000000.0   
2616                   857803.65                   4200000.0   
2617                   904045.87                   9500000.0   
2618                  4906702.85                  75000000.0   
2619                   617486.59                   3000000.0   

      Minimum_Transaction_Amount  Average_Transaction_Frequency       Range  \
0                        28900.0                           1.53   2271100.0   
1                        50000.0                           1.47    450000.0   
2                        30000.0                           2.60   6970000.0   
3                        26500.0                           2.56   4973500.0   
4                        25000.0                           3.05  98975000.0   
...                          ...                            ...         ...   
2615                     47500.0                           1.90   9952500.0   
2616                    100000.0                           2.18   4100000.0   
2617          

# Conclusion

Setelah melakukan binning untuk membentuk model yang kemudian dilanjutkan dengan melakukan beberapa macam algortima dengan menggunakan h2o maupun tidak, hasil terbaik yang bisa kami simpulkan untuk prediksi ialah menggunakan model dari algoritma Gradient Boosting yang dibentuk dari hasil h2o. Hal ini dikarenakan nilai f1 pada Gradient Boosting lebih besar dibandingkan algoritma lain dengan nilai f1 sebesar 0,48 dan akurasi sebesar 0,93.